In [1]:
import pandas as pd
import re
import math
import requests
import json

In [2]:
df = pd.read_csv('phishing_site_urls.csv')
df.head()

URL Label
0  nobell.it/70ffb52d079109dca5664cce6f317373782/...   bad
1  www.dghjdgf.com/paypal.co.uk/cycgi-bin/webscrc...   bad
2  serviciosbys.com/paypal.cgi.bin.get-into.herf....   bad
3  mail.printakid.com/www.online.americanexpress....   bad
4  thewhiskeydregs.com/wp-content/themes/widescre...   bad

In [3]:
# @Globals
tldSet = set()
bad_url_word_frequency = {}
good_url_word_frequency = {}
sensitive_words = []

In [ ]:
def count_digits(word):
  return len(re.findall('[0-9]', word))

def count_alphabets(word):
  return len(re.findall('[A-z]', word))

In [4]:
def remove_special_characters(input_string):
  # Pattern to match any non-alphanumeric and non-space character
  pattern = r'[^a-zA-Z0-9\s]'  
  return re.sub(pattern, '', input_string)

In [5]:
def calculate_entropy(word):
  if len(word) == 0:
    return 0

  entropy = 0
  word_length = len(word)
  char_count = {}

  for char in word:
    if char in char_count:
      char_count[char] += 1
    else:
      char_count[char] = 1

  for char in char_count:
    probability = char_count[char] / word_length
    entropy += -probability * math.log2(probability)

  return entropy

In [6]:
# https://www.whoisxmlapi.com/whoisserver/WhoisService?apiKey=at_BGLU4RpM0fcKHpqsqHAYRWFl4bIt2&domainName=facebook.com

# API Key: at_BGLU4RpM0fcKHpqsqHAYRWFl4bIt2
# Rapid API Key: d2592fe48dmsh190428470dadf9cp1bf762jsnf40816e6115e (Shauryansingh23102001@gmail.com)

def whois_api_request(domain_url):
    url = "https://whoisapi-whois-v2-v1.p.rapidapi.com/whoisserver/WhoisService"

    headers = {
	    "X-RapidAPI-Key": "d2592fe48dmsh190428470dadf9cp1bf762jsnf40816e6115e",
	    "X-RapidAPI-Host": "whoisapi-whois-v2-v1.p.rapidapi.com"
    }

    querystring = {
        "domainName":domain_url,
        "apiKey":"at_BGLU4RpM0fcKHpqsqHAYRWFl4bIt2",
        "outputFormat":"JSON",
        "da":"0",
        "ipwhois":"1",
        "thinWhois":"0",
        "_parse":"0",
        "preferfresh":"1",
        "checkproxydata":"0",
        "ip":"1"
    }
    
    response = requests.get(url, headers=headers, params=querystring)
    response_text = response.text

    return response_text

In [ ]:
"""
for (index, colname) in enumerate(df):
  if(index == 2500):
    break

  URL = df["URL"].values
  domain = URL.split("/")[0]
  url_length = len(URL)
  domain_entropy = calculate_entropy(domain)

  # Top Level Domain Extraction Logic
  tld = domain.split(".")[-1]
  tld_length = len(tld)
  tld = tld.split(":")[0]
  tld = tld.split("-")[0]
  if(tld_length > 1 and tld_length < 10 and count_alphabets(tld) > count_digits(tld)):
    tldSet.add(tld)

  if df["Label"].values == "bad":
    temp = URL.split("/")
    subdomain = "/".join(temp[1:])
    words_list = re.split("[/,.,?,-,+,=,&,~,!,@,#,$,%,_,;]", subdomain)
    for word in words_list:
      word = word.strip().lower()
      word = remove_special_characters(word)
      digs = len(re.findall('[0-9]', word))
      alps = len(re.findall('[A-z]', word))
      if(len(word) < 2 or len(word) > 15 or digs > alps):
        continue
      if word in bad_url_word_frequency:
        bad_url_word_frequency[word] += 1
      else:
        bad_url_word_frequency[word] = 1
  else:
    temp = URL.split("/")
    subdomain = "/".join(temp[1:])
    words_list = re.split("[/,.,?,-,+,=,&,~,!,@,#,$,%,_,;]", subdomain)
    for word in words_list:
      word = word.strip().lower()
      word = remove_special_characters(word)
      digs = len(re.findall('[0-9]', word))
      alps = len(re.findall('[A-z]', word))
      if(len(word) < 2 or len(word) > 15 or digs > alps):
        continue
      if word in good_url_word_frequency:
        good_url_word_frequency[word] += 1
      else:
        good_url_word_frequency[word] = 1

print(len(good_url_word_frequency))
print(len(bad_url_word_frequency))
"""

In [8]:
# Iterate all rows using DataFrame.iterrows()
for index, row in df.iterrows():
  # if(index == 2500):
  #   break

  URL = row["URL"]
  label = row["Label"]
  domain = URL.split("/")[0]
  url_length = len(URL)
  domain_entropy = calculate_entropy(domain)

  # Top Level Domain Extraction Logic
  # tld = domain.split(".")[-1]
  # tld_length = len(tld)
  # tld = tld.split(":")[0]
  # tld = tld.split("-")[0]
  # if(tld_length > 1 and tld_length < 10 and count_alphabets(tld) > count_digits(tld)):
  #   tldSet.add(tld)

  temp = URL.split("/")
  subdomain = "/".join(temp[1:])
  words_list = re.split("[/,.,?,-,+,=,&,~,!,@,#,$,%,_,;]", subdomain)
  
  # Create Word Frequency for Good and Bad URLs
  if label == "bad":
    for word in words_list:
      word = word.strip().lower()
      word = remove_special_characters(word)
      digs = len(re.findall('[0-9]', word))
      alps = len(re.findall('[A-z]', word))
      
      if(len(word) > 2 or len(word) < 15 or digs < alps):  
        if word in bad_url_word_frequency:
          bad_url_word_frequency[word] += 1
        else:
          bad_url_word_frequency[word] = 1
  else:
    for word in words_list:
      word = word.strip().lower()
      word = remove_special_characters(word)
      digs = len(re.findall('[0-9]', word))
      alps = len(re.findall('[A-z]', word))
      
      if(len(word) > 2 or len(word) < 15 or digs < alps):
        if word in good_url_word_frequency:
          good_url_word_frequency[word] += 1
        else:
          good_url_word_frequency[word] = 1

# sorted_good_url_word_frequency = sorted(good_url_word_frequency.items(), key=lambda x:x[1], reverse=True)
# sorted_bad_url_word_frequency = sorted(bad_url_word_frequency.items(), key=lambda x:x[1], reverse=True)

print(len(good_url_word_frequency))
print(len(bad_url_word_frequency))

319631
80071


In [9]:
for it in good_url_word_frequency:
  print(it)

js
index
htm
us
battle
net
noghn
en

ref5m
9dbbws
btnefnud
jyjplr
cmp
6
ptp8
iq
jqdvtsrdigv yfkfv

xmyrs	
kizbtu9em qlmj
ceel
l
xh6
7ju gip9oitvd
k
hioo0c
f
d16 g
2p9ip

vz3a vwk
sd7na0qftjw2xhtiu
 scyjld64r
u
6amp
offerid
newmailenusv2
amp
sitestate
ver4
yeu
6rtu
g0mi
xz
fn
7u1fw
ct0jev2p
jlwjpsiv
o
p h
3
crqbgz dmqx
9
btmnpmq

audbq
vurh
7
2
4j91
web
media
syqvem
dkij
rgr05dfecmg
gh
cb 
l pl 
akzhz
tbua

arg
qkc
 sqnvo4zcge
zh2tvxqxnpmdx
anaacbajl  mxxu4
xebo7
images
as
vies
1i75cf7b16vcfd16b96g
sd
6vd909qt5 n
s

r7
m06e5zw0kmod
c1hdeee
e
hyuu7m
jvbs
u5kpg9yk
dsg34ex
onhaipvr2y7
login
ref
ifezuzrus
d3
in
ex
ao
l1pcmd3b 0070
phw
xyoyvn
i
fysotiwn
f
cb
ne 5iutvi4cq a	e8lc5z3ffji
zzzt hp6lst
g1c
7qv
mtnyfgjus
battl
nat
addx
101
0
007
a4
niw43l
x km
ipp7
rw
xxcb
db2y
bohlezhus
ijfgx
00000p
n1
q
766
2t
y
frgg2
ny
tw3z2
xcpabk
djyxt9
logmn
2ef
thfhvbnus
cawlg4getd7
n
meyep
mv3yw
f	nx
g i3atii
r6
rdf
h4p
3a
2f
2fbml
w
bqule
led
dfltom5dangovcgueo
j2
m

In [ ]:
for it in bad_url_word_frequency:
    print(it)

In [ ]:
for it in good_url_word_frequency:
  if(it[1] > 5):
    sensitive_words.append(it)

In [ ]:
with open('top_level_domains.txt', 'w', encoding='utf-8') as file:
    for item in tldSet:
        file.write(str(item) + '\n')

In [ ]:
for it in bad_url_word_frequency:
  if(it[1] > 5):
    sensitive_words.append(it)

#### *** Export Sensitive Words to a file. Only the words sensitive_words[0] *** ###
#### *** Loop through good label rows to export their TLD to a file *** ###

In [ ]:
with open('output.txt', 'w') as file:
  for item in sensitive_words:
    file.write(str(item) + '\n')

In [ ]:
# https://www.whoisxmlapi.com/whoisserver/WhoisService?apiKey=at_BGLU4RpM0fcKHpqsqHAYRWFl4bIt2&domainName=facebook.com

# API Key: at_BGLU4RpM0fcKHpqsqHAYRWFl4bIt2
# Rapid API Key: d2592fe48dmsh190428470dadf9cp1bf762jsnf40816e6115e (Shauryansingh23102001@gm)

url = "https://whoisapi-whois-v2-v1.p.rapidapi.com/whoisserver/WhoisService"

domain_url_name = "youtube.com"

querystring = {
  "domainName":domain_url_name,
  "apiKey":"at_BGLU4RpM0fcKHpqsqHAYRWFl4bIt2",
  "outputFormat":"JSON",
  "da":"0",
  "ipwhois":"1",
  "thinWhois":"0",
  "_parse":"0",
  "preferfresh":"1",
  "checkproxydata":"0",
  "ip":"1"
  }

headers = {
	"X-RapidAPI-Key": "d2592fe48dmsh190428470dadf9cp1bf762jsnf40816e6115e",
	"X-RapidAPI-Host": "whoisapi-whois-v2-v1.p.rapidapi.com"
}

response = requests.get(url, headers=headers, params=querystring)

print(response.json())

### Important Attributes From WHOIS API
---
createdDate: Date Format String

updatedDate: Date Format String

expiresDate: Date Format String

registrant.countryCode : String

registrarName: String

domainNameExt: String

estimatedDomainAge : Int

ips : Array[STRING]

registrarIANAID

Nameservers: 

Check if nameservers are from reputable hosting providers

In [ ]:
response_text = response.text

In [ ]:
with open("output1.json", "w") as file:
  # Write the response content to the file
  file.write(response_text)

In [ ]:
print(type(response))
print(type(response_text))